# Alineación de Preferencias con Optimización de Preferencias por Ratio de Probabilidades (ORPO)

Este notebook te guiará en el proceso de fine-tuning de un modelo de lenguaje utilizando la Optimización de Preferencias por Ratio de Probabilidades (Odds Ratio Preference Optimization (ORPO)). Usaremos el modelo **SmolLM2-135M**, el cual **no** ha sido sometido al entrenamiento SFT, haciéndolo incompatible con DPO. Por tanto, no podrás usar el modelo que entrenaste en [1_instruction_tuning](../../1_instruction_tuning/notebooks/sft_finetuning_example.ipynb).

<div style='background-color: lightblue; padding: 10px; border-radius: 5px; margin-bottom: 20px; color:black'>
     <h2 style='margin: 0;color:blue'>Ejercicio: Alinea SmolLM2 con DPOTrainer</h2>
     <p>Elige un dataset del hub de Hugging Face y alinea un modelo con él.</p> 
     <p><b>Niveles de Dificultad</b></p>
     <ul>
         <li>🐢 Usa el dataset `trl-lib/ultrafeedback_binarized`</li>
         <li>🐕 Prueba el dataset `argilla/ultrafeedback-binarized-preferences`</li>
         <li>🦁 Trabaja con un subconjunto del dataset `mlabonne/orpo-dpo-mix-40k`</li>
     </ul>
</div>


## Importa las librerías


In [ ]:
import torch
import os
from datasets import load_dataset
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
)
from trl import ORPOConfig, ORPOTrainer, setup_chat_format

# Autenticación en Hugging Face
from huggingface_hub import login

login()

/Users/ben/code/smol-course/.venv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Formatea el conjunto de datos

In [ ]:
# Carga el conjunto de datos

# TODO: 🦁🐕 cambia el conjunto de datos a uno de tu elección.
dataset = load_dataset(path="trl-lib/ultrafeedback_binarized", split="train")

Generating test split: 100%|██████████| 1000/1000 [00:00<00:00, 382866.64 examples/s]


In [ ]:
# TODO: 🐕 Si tu conjunto de datos no está estructurado como listas de conversaciones, puedes usar la función `process_dataset` para convertirlo.

## Define el modelo

In [ ]:
model_name = "HuggingFaceTB/SmolLM2-135M"

device = (
    "cuda"
    if torch.cuda.is_available()
    else "mps" if torch.backends.mps.is_available() else "cpu"
)

# Modelo para afinar
model = AutoModelForCausalLM.from_pretrained(
    pretrained_model_name_or_path=model_name,
    torch_dtype=torch.float16,
).to(device)
model.config.use_cache = False
tokenizer = AutoTokenizer.from_pretrained(model_name)
model, tokenizer = setup_chat_format(model, tokenizer)

# Establece el nombre para guardar o subir el modelo afinado
finetune_name = "SmolLM2-FT-DPO"
finetune_tags = ["smol-course", "module_2"]

## Entrena el modelo con ORPO

In [ ]:
orpo_args = ORPOConfig(
    # Tasa de aprendizaje baja para evitar el olvido catastrófico
    learning_rate=8e-6,
    # Decaimiento lineal de la tasa de aprendizaje durante el entrenamiento
    lr_scheduler_type="linear",
    # Longitud máxima combinada de prompt + respuesta
    max_length=1024,
    # Longitud máxima para los prompts de entrada
    max_prompt_length=512,
    # Controla el peso de la pérdida del ratio de probabilidades (λ en el artículo)
    beta=0.1,
    # Tamaño del lote para el entrenamiento
    per_device_train_batch_size=2,
    per_device_eval_batch_size=2,
    # Ayuda con la estabilidad del entrenamiento acumulando gradientes antes de actualizar
    gradient_accumulation_steps=4,
    # Optimizador eficiente en memoria para CUDA, vuelve a adamw_torch en CPU/MPS
    optim="paged_adamw_8bit" if device == "cuda" else "adamw_torch",
    # Número de épocas de entrenamiento
    num_train_epochs=1,
    # Cuándo ejecutar la evaluación
    evaluation_strategy="steps",
    # Evalua cada 20% del entrenamiento
    eval_steps=0.2,
    # Registra las métricas en cada paso
    logging_steps=1,
    # Calentamiento gradual de la tasa de aprendizaje
    warmup_steps=10,
    # Desactivar registro externo
    report_to="none",
    # Dónde guardar el modelo/puntos de control
    output_dir="./results/",
    # Habilitar MPS (Metal Performance Shaders) si está disponible
    use_mps_device=device == "mps",
    hub_model_id=finetune_name,
)

In [ ]:
trainer = ORPOTrainer(
    model=model,
    args=orpo_args,
    train_dataset=dataset["train"],
    eval_dataset=dataset["test"],
    processing_class=tokenizer,
)

In [ ]:
trainer.train()  # Entrena el modelo

# Guarda el modelo
trainer.save_model(f"./{finetune_name}")

# Sube el modelo a Hugging Face si el inicio de sesión o HF_TOKEN está configurado
if os.getenv("HF_TOKEN"):
    trainer.push_to_hub(tags=finetune_tags)

## 💐 ¡Has terminado!

Este notebook ofrece una guía paso a paso para realizar fine-tuning al modelo `HuggingFaceTB/SmolLM2-135M` utilizando el `ORPOTrainer`. Siguiendo estos pasos, puedes adaptar el modelo para realizar tareas específicas de manera más efectiva. Si deseas continuar trabajando en este curso, aquí tienes algunos pasos que podrías intentar:

- Prueba este notebook en un nivel de dificultad más alto.  
- Revisa el PR de un colega.  
- Mejora el material del curso a través de un Issue o PR.  